In [1]:
import pandas as pd
from ch2.data import *
from ch2.squeal.database import connect

s = session('-v 0')
raw = activity_statistics(s, SPEED, DISTANCE, ELEVATION, CADENCE, LATITUDE, LONGITUDE, HEART_RATE,
                         local_time='2018-01-16 12:00', activity_group_name='Bike', with_timespan=True)
raw.describe()

Timespan ID     Latitude    Longitude        Speed      Distance  \
count   2311.000000  2311.000000  2311.000000  2311.000000   2311.000000   
mean   15892.517525   -33.344065   -70.503079     5.776180  38091.234479   
std        7.501256     0.037118     0.047217     2.359839  20038.745664   
min    15817.000000   -33.427446   -70.611250     0.000000      4.860000   
25%    15886.500000   -33.377510   -70.538338     4.576500  22816.870000   
50%    15894.000000   -33.331681   -70.477016     5.822000  39342.380000   
75%    15895.000000   -33.314070   -70.470489     7.161500  52234.785000   
max    15906.000000   -33.289474   -70.453889    14.229000  75357.890000   

           Cadence   Heart Rate    Elevation  
count  2308.000000  2311.000000  2287.000000  
mean     59.011265   121.017309  1135.107528  
std      45.584932    11.830793   396.117057  
min       0.000000    82.000000   616.376105  
25%       0.000000   113.000000   762.764162  
50%      86.500000   121.000000  1035.741355  
75%      98.000000   129.000000  1524.340278  
max     125.000000   153.000000  1814.388717

In [2]:
from ch2.data.power import *

df = linear_resample(raw)
df = add_differentials(df)
df = add_energy_budget(df, m=64+12)
df = add_air_speed(df, 0, 0)
df = add_loss_estimate(df)
df = add_power_estimate(df)
print(measure_initial_scaling(df))
df = add_modeled_hr(df, -99, 0.3, 121, 45)


(-99, 0.05248935988022496, 120.26712453318596, 45.0)


In [6]:
model = fit_power(df, PowerModel(cda=0.45, log_adaption=-99, slope=0.05, intercept=121, delay=45), 
                  'slope', 'intercept', 'log_adaption', 'delay')
print(model)

PowerModel(cda=0.45, crr=0, slope=0.21876895339595717, intercept=96.9705005284912, log_adaption=-13.972042717384557, delay=18.721520507939758, m=70, wind_speed=0, wind_heading=0)


In [7]:
df = add_modeled_hr(df, -14, 0.2, 97, 19)

In [10]:
from bokeh.plotting import output_notebook, show
from bokeh.layouts import row, column

from ch2.data.plot import *

output_notebook()
df['error'] = df[DETRENDED_HEART_RATE] - df[PREDICTED_HEART_RATE]
show(column([comparison_line_plot(700, 200, TIME, y, df) 
             for y in (POWER, HEART_RATE, DETRENDED_HEART_RATE, PREDICTED_HEART_RATE, 'error')]))


Loading BokehJS ...